In [1]:
#!git clone -b qwen3_moe https://github.com/kIshizaki-sci/AutoAWQ.git
!pip install -U transformers hf_xet
!pip install -e ./AutoAWQ

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.4/10.4 MB 140.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.6/53.6 MB 234.7 MB/s eta 0:00:0000:01
  Attempting uninstall: huggingface-hub
    Found existing installation: huggingface-hub 0.29.1
    Uninstalling huggingface-hub-0.29.1:
      Successfully uninstalled huggingface-hub-0.29.1
  Attempting uninstall: transformers
    Found existing installation: transformers 4.49.0
    Uninstalling transformers-4.49.0:
      Successfully uninstalled transformers-4.49.0

[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python -m pip install --upgrade pip
Obtaining file:///workspace/AutoAWQ
  Preparing metadata (setup.py) ... one
  Attempting uninstall: autoawq
    Found existing installation: autoawq 0.2.7.post3
    Uninstalling autoawq-0.2.7.post3:
      Successfully uninstalled autoawq-0.2.7.post3
  DEPRECATION: Legacy editable install of autoawq==0.2.8 from file:///workspace/AutoAWQ (setup

In [1]:
import torch
import transformers
from awq import AutoAWQForCausalLM
from transformers import AutoTokenizer, AutoModelForCausalLM, AutoConfig
import torch

print('torch version : ', torch.__version__)
print('transformers version : ', transformers.__version__)

torch version :  2.4.1+cu124
transformers version :  4.51.3


In [2]:
%%time
model = AutoAWQForCausalLM.from_quantized("kishizaki-sci/Qwen3-30B-A3B-FP16-AWQ-multi-scale", use_cache=True, device_map='auto')
tokenizer = AutoTokenizer.from_pretrained("kishizaki-sci/Qwen3-30B-A3B-FP16-AWQ-multi-scale")

Fetching 15 files:   0%|          | 0/15 [00:00<?, ?it/s]

Replacing layers...: 100%|██████████| 48/48 [00:18<00:00,  2.56it/s]
/workspace/AutoAWQ/awq/models/base.py:541: UserWarning: Skipping fusing modules because AWQ extension is not installed.No module named 'awq_ext'
  warnings.warn("Skipping fusing modules because AWQ extension is not installed." + msg)


CPU times: user 1min 21s, sys: 4.84 s, total: 1min 26s
Wall time: 1min 27s


In [3]:
model.model

Qwen3MoeForCausalLM(
  (model): Qwen3MoeModel(
    (embed_tokens): Embedding(151936, 2048)
    (layers): ModuleList(
      (0-47): 48 x Qwen3MoeDecoderLayer(
        (self_attn): Qwen3MoeAttention(
          (q_proj): WQLinear_GEMM(in_features=2048, out_features=4096, bias=False, w_bit=4, group_size=128)
          (k_proj): WQLinear_GEMM(in_features=2048, out_features=512, bias=False, w_bit=4, group_size=128)
          (v_proj): WQLinear_GEMM(in_features=2048, out_features=512, bias=False, w_bit=4, group_size=128)
          (o_proj): WQLinear_GEMM(in_features=4096, out_features=2048, bias=False, w_bit=4, group_size=128)
          (q_norm): Qwen3MoeRMSNorm((128,), eps=1e-06)
          (k_norm): Qwen3MoeRMSNorm((128,), eps=1e-06)
        )
        (mlp): Qwen3MoeSparseMoeBlock(
          (gate): WQLinear_GEMM(in_features=2048, out_features=128, bias=False, w_bit=4, group_size=128)
          (experts): ModuleList(
            (0-127): 128 x Qwen3MoeMLP(
              (gate_proj): WQLinear

In [4]:
config = AutoConfig.from_pretrained("kishizaki-sci/Qwen3-30B-A3B-FP16-AWQ-multi-scale")
config

Qwen3MoeConfig {
  "architectures": [
    "Qwen3MoeForCausalLM"
  ],
  "attention_bias": false,
  "attention_dropout": 0.0,
  "bos_token_id": 151643,
  "decoder_sparse_step": 1,
  "eos_token_id": 151645,
  "head_dim": 128,
  "hidden_act": "silu",
  "hidden_size": 2048,
  "initializer_range": 0.02,
  "intermediate_size": 6144,
  "max_position_embeddings": 40960,
  "max_window_layers": 48,
  "mlp_only_layers": [],
  "model_type": "qwen3_moe",
  "moe_intermediate_size": 768,
  "norm_topk_prob": true,
  "num_attention_heads": 32,
  "num_experts": 128,
  "num_experts_per_tok": 8,
  "num_hidden_layers": 48,
  "num_key_value_heads": 4,
  "output_router_logits": false,
  "quantization_config": {
    "bits": 4,
    "group_size": 128,
    "modules_to_not_convert": null,
    "quant_method": "awq",
    "version": "gemm",
    "zero_point": true
  },
  "rms_norm_eps": 1e-06,
  "rope_scaling": null,
  "rope_theta": 1000000.0,
  "router_aux_loss_coef": 0.001,
  "sliding_window": null,
  "tie_word_embe

In [5]:
# prepare the model input
prompt = "Give me a short introduction to large language model."
messages = [
    {"role": "user", "content": prompt}
]
text = tokenizer.apply_chat_template(
    messages,
    tokenize=False,
    add_generation_prompt=True,
    enable_thinking=True # Switches between thinking and non-thinking modes. Default is True.
)
model_inputs = tokenizer([text], return_tensors="pt").to(model.model.device)

In [6]:
model_inputs

{'input_ids': tensor([[151644,    872,    198,  35127,    752,    264,   2805,  16800,    311,
           3460,   4128,   1614,     13, 151645,    198, 151644,  77091,    198]],
       device='cuda:0'), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]],
       device='cuda:0')}

In [7]:
%%time
generated_ids = model.generate(
    **model_inputs,
    max_new_tokens=32768
)

Setting `pad_token_id` to `eos_token_id`:151645 for open-end generation.


CPU times: user 15min 10s, sys: 1.33 s, total: 15min 11s
Wall time: 15min 11s


In [8]:
output_ids = generated_ids[0][len(model_inputs.input_ids[0]):].tolist() 

# parsing thinking content
try:
    # rindex finding 151668 (</think>)
    index = len(output_ids) - output_ids[::-1].index(151668)
except ValueError:
    index = 0

thinking_content = tokenizer.decode(output_ids[:index], skip_special_tokens=True).strip("\n")
content = tokenizer.decode(output_ids[index:], skip_special_tokens=True).strip("\n")

print("thinking content:", thinking_content)
print("content:", content)

thinking content: 
content: View

Okay, the user is asking for a short introduction to large language models. Let me start by defining what they are. I should mention that they're AI models trained on a lot of text data. Maybe start with the basics: they're a type of artificial intelligence, specifically in the field of natural language processing.

I need to explain their purpose. They can generate text, answer questions, translate, and more. It's important to note that they're "large" because they have a huge number of parameters, which makes them more powerful but also more complex. I should explain the term "large" in their name refers to the scale of their training data and model size.

Also, I should touch on their applications. They're used in various tasks like chatbots, content creation, data analysis, and more. Maybe give a few examples of companies or models, like GPT, BERT, or others. But keep it brief as the user wants a short intro.

I should also mention the benefits, li

In [9]:
!nvidia-smi

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


Sun May  4 15:59:34 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 565.57.01              Driver Version: 565.57.01      CUDA Version: 12.7     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA A100-SXM4-80GB          On  |   00000000:07:00.0 Off |                    0 |
| N/A   26C    P0             82W /  400W |   20625MiB /  81920MiB |      0%      Default |
|                                         |                        |             Disabled |
+-----------------------------------------+-----